#<center>Assignemnt-2</center>


### Group Number: 14
### Members Roll Numbers: 24AI60R13, 24AI60R46


## Libraries and device checking

In [1]:
print("Installing all required libraries")
!pip install torch
!pip install torch-geometric
!pip install karateclub
!pip install node2vec
!pip install tqdm


Installing all required libraries
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.1/63.1 kB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 15.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.5/64.5 kB 3.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 25.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 81.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.5/11.5 MB 86.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 56.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.4/177.4 kB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 73.1 MB/s eta 0:00:00
  Created wheel for karateclub: filename=karateclub-1.3.3-py3-none-any.whl size=101980 sha256=8d874141bb20b85a3779f3fbaaf5bda8a02657ba5afc13bc52c6d75e9036bca9
  Stored in directory: /root/.cache/pip/wheels/62/bd/af/17e

  Using cached networkx-3.3-py3-none-any.whl.metadata (5.1 kB)
  Using cached numpy-1.26.4-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (61 kB)
Using cached networkx-3.3-py3-none-any.whl (1.7 MB)
Using cached numpy-1.26.4-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (18.2 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.22.4
    Uninstalling numpy-1.22.4:
      Successfully uninstalled numpy-1.22.4
  Attempting uninstall: networkx
    Found existing installation: networkx 2.6.3
    Uninstalling networkx-2.6.3:
      Successfully uninstalled networkx-2.6.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
arviz 0.18.0 requires pandas>=1.5.0, but you have pandas 1.3.5 which is incompatible.
cudf-cu12 24.4.1 requires pandas<2.2.2dev0,>=2.0, but you have pandas 1.3.5 which is incompatible.
geopandas 0.14.

In [2]:
import torch
import torch_geometric
import matplotlib.pyplot as plt
import numpy as np
from torch.utils.data import random_split
from torch_geometric.datasets import QM9
from torch_geometric.data import DataLoader
from torch_geometric.nn import MessagePassing
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch_geometric.nn import MessagePassing
from torch_geometric.utils import add_self_loops, degree

Checking the device so that if GPU is available the compution will be very fast

In [3]:
print("Updating Status in 'device' Variable")
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Device available is: {device}")

Updating Status in 'device' Variable
Device available is: cpu


## Data Loading

In [29]:
import torch
from torch_geometric.datasets import QM9

print("Specifing the path where dataset will be stored")
dataset_path = '/data/QM9/'

Specifing the path where dataset will be stored


In [30]:
print("Loading the QM9 dataset")
dataset = QM9(root=dataset_path)

Loading the QM9 dataset


Extracting /data/QM9/raw/qm9_v3.zip
Processing...
Using a pre-processed version of the dataset. Please install 'rdkit' to alternatively process the raw data.
Done!


In [31]:
print("Cheking if graph loaded successfully with first graph data")
data = dataset[0]

Cheking if graph loaded successfully with first graph data


In [32]:
num_graphs = len(dataset)
print(f"Number of graphs in the dataset: {num_graphs}")

Number of graphs in the dataset: 130831


In [33]:

num_node_features = data.x.shape[1]
print(f"Number of features per node: {num_node_features}")

Number of features per node: 11


In [34]:

num_edge_features = data.edge_attr.shape[1]
print(f"Number of edge features: {num_edge_features}")

Number of edge features: 4


In [35]:

num_nodes_first_graph = data.num_nodes
print(f"Number of nodes in the first graph: {num_nodes_first_graph}")

Number of nodes in the first graph: 5


In [36]:

num_edges_first_graph = data.num_edges
print(f"Number of edges in the first graph: {num_edges_first_graph}")

Number of edges in the first graph: 8


In [37]:

num_edge_features_first_graph = data.edge_attr.size()
print(f"Number of edge features in the first graph: {num_edge_features_first_graph}")

Number of edge features in the first graph: torch.Size([8, 4])


In [38]:
print("Testing extraction logic for first graph")

data_graph_1 = dataset[0]
dipole_moment = data_graph_1.y[0][0].item()
print(f'Dipole moment for the first graph: {dipole_moment}')

Testing extraction logic for first graph
Dipole moment for the first graph: 0.0


In [40]:
print("Seprating required target value for 1200 graphs only")
dipole_moments = []
total_graph = 1200
for i in range(min(total_graph, len(dataset))):
    data = dataset[i]
    dipole_moment = data.y[0][0].item()
    dipole_moments.append(dipole_moment)

target_tensor = torch.tensor(dipole_moments)

Seprating required target value for 1200 graphs only


In [41]:
# Creating a DataLoader

def create_dataloader(dataset, batch_size=50, shuffle=True):
    return DataLoader(dataset, batch_size=batch_size, shuffle=shuffle)

train_loader = create_dataloader(dataset[:1000])  # Using a subset for demonstration
val_loader = create_dataloader(dataset[1000:1100],shuffle=False)
test_loader = create_dataloader(dataset[1100:1200],shuffle=False)

print(f"Number of batches in train_loader: {len(train_loader)}")
print(f"Number of batches in val_loader: {len(val_loader)}")
print(f"Number of batches in test_loader: {len(test_loader)}")

Number of batches in train_loader: 20
Number of batches in val_loader: 2
Number of batches in test_loader: 2


## Part A


In [43]:
print("Importing libraries")
import torch
import numpy as np
from tqdm import tqdm
from karateclub import DeepWalk
from node2vec import Node2Vec
from torch_geometric.utils import to_networkx
from torch_geometric.data import DataLoader

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

def generate_embeddings_batch(graphs, embedding_dimensions, walk_length, num_walks, p, q, device):
    all_embeddings = []

    for i, graph_data in tqdm(enumerate(graphs), desc='Processing Graphs', unit='graph', total=len(graphs)):
        # Convert to networkx graph
        G = to_networkx(graph_data, to_undirected=True)

        if p == 1 and q == 1:
            # Use DeepWalk
            model = DeepWalk(n_steps=walk_length, n_walks=num_walks, dimensions=embedding_dimensions)
            model.fit(G)
            embeddings = [model.wv[str(node)] for node in G.nodes()]
        else:
            # Use Node2Vec
            node2vec = Node2Vec(
                graph=G,
                dimensions=embedding_dimensions,
                walk_length=walk_length,
                num_walks=num_walks,
                p=p,
                q=q
            )
            model = node2vec.fit(window=10, min_count=1, batch_words=4)
            embeddings = [model.wv[str(node)] for node in G.nodes()]

        # Convert embeddings to tensor
        embeddings_tensor = torch.tensor(embeddings, dtype=torch.float32).to(device)
        all_embeddings.append(embeddings_tensor.cpu())

    return all_embeddings

def process_batch_embeddings(data_loader, embedding_dimensions, walk_length, num_walks, p, q, device):
    batch_embeddings = []

    for batch in tqdm(data_loader, desc='Processing Batches', unit='batch'):
        # Extract graphs from batch
        if isinstance(batch, tuple):
            graphs = [data for data in batch]
        else:
            graphs = [batch]

        embeddings = generate_embeddings_batch(
            graphs,
            embedding_dimensions=embedding_dimensions,
            walk_length=walk_length,
            num_walks=num_walks,
            p=p,
            q=q,
            device=device
        )
        batch_embeddings.extend(embeddings)

    return batch_embeddings

embedding_dimensions = 64
walk_length = 10
num_walks = 50
p = 1
q = 0.5
batch_size = 200  # Adjust based on your GPU memory

# Process embeddings
train_embeddings = process_batch_embeddings(train_loader, embedding_dimensions, walk_length, num_walks, p, q, device)
val_embeddings = process_batch_embeddings(val_loader, embedding_dimensions, walk_length, num_walks, p, q, device)
test_embeddings = process_batch_embeddings(test_loader, embedding_dimensions, walk_length, num_walks, p, q, device)

print(f"Number of train embeddings: {len(train_embeddings)}")
print(f"Number of validation embeddings: {len(val_embeddings)}")
print(f"Number of test embeddings: {len(test_embeddings)}")


Importing libraries


Processing Graphs:   0%|          | 0/1 [00:00<?, ?graph/s]

Computing transition probabilities:   0%|          | 0/609 [00:00<?, ?it/s]



Generating walks (CPU: 1):   0%|          | 0/50 [00:00<?, ?it/s]

Generating walks (CPU: 1):   8%|▊         | 4/50 [00:00<00:01, 29.48it/s]

Generating walks (CPU: 1):  14%|█▍        | 7/50 [00:00<00:01, 23.32it/s]

Generating walks (CPU: 1):  20%|██        | 10/50 [00:00<00:01, 20.91it/s]

Generating walks (CPU: 1):  26%|██▌       | 13/50 [00:00<00:01, 20.13it/s]

Generating walks (CPU: 1):  32%|███▏      | 16/50 [00:00<00:01, 18.51it/s]

Generating walks (CPU: 1):  38%|███▊      | 19/50 [00:00<00:01, 19.15it/s]

Generating walks (CPU: 1):  42%|████▏     | 21/50 [00:01<00:01, 17.88it/s]

Generating walks (CPU: 1):  48%|████▊     | 24/50 [00:01<00:01, 20.25it/s]

Generating walks (CPU: 1):  54%|█████▍    | 27/50 [00:01<00:01, 22.31it/s]

Generating walks (CPU: 1):  60%|██████    | 30/50 [00:01<00:00, 23.80it/s]

Generating walks (CPU: 1):  68%|██████▊   | 34/50 [00:01<00:00, 27.97it/s]

Generating walks (CPU: 1):  76%|███████▌  | 38/50 [00:01<00:00, 30.21it/s]

Generating walks (CPU

Computing transition probabilities:   0%|          | 0/633 [00:00<?, ?it/s]

...

Computing transition probabilities:   0%|          | 0/806 [00:00<?, ?it/s]



Generating walks (CPU: 1):   0%|          | 0/50 [00:00<?, ?it/s]

Generating walks (CPU: 1):   6%|▌         | 3/50 [00:00<00:02, 21.59it/s]

Generating walks (CPU: 1):  12%|█▏        | 6/50 [00:00<00:02, 17.65it/s]

Generating walks (CPU: 1):  16%|█▌        | 8/50 [00:00<00:02, 17.18it/s]

Generating walks (CPU: 1):  20%|██        | 10/50 [00:00<00:02, 17.12it/s]

Generating walks (CPU: 1):  24%|██▍       | 12/50 [00:00<00:02, 16.60it/s]

Generating walks (CPU: 1):  28%|██▊       | 14/50 [00:00<00:02, 16.61it/s]

Generating walks (CPU: 1):  32%|███▏      | 16/50 [00:00<00:02, 16.53it/s]

Generating walks (CPU: 1):  36%|███▌      | 18/50 [00:01<00:01, 16.39it/s]

Generating walks (CPU: 1):  40%|████      | 20/50 [00:01<00:01, 15.31it/s]

Generating walks (CPU: 1):  44%|████▍     | 22/50 [00:01<00:01, 15.15it/s]

Generating walks (CPU: 1):  48%|████▊     | 24/50 [00:01<00:01, 15.26it/s]

Generating walks (CPU: 1):  52%|█████▏    | 26/50 [00:01<00:01, 15.31it/s]

Generating walks (CPU:

Computing transition probabilities:   0%|          | 0/728 [00:00<?, ?it/s]



Generating walks (CPU: 1):   0%|          | 0/50 [00:00<?, ?it/s]

Generating walks (CPU: 1):   8%|▊         | 4/50 [00:00<00:01, 33.42it/s]

Generating walks (CPU: 1):  16%|█▌        | 8/50 [00:00<00:01, 28.21it/s]

Generating walks (CPU: 1):  22%|██▏       | 11/50 [00:00<00:01, 28.86it/s]

Generating walks (CPU: 1):  30%|███       | 15/50 [00:00<00:01, 29.80it/s]

Generating walks (CPU: 1):  38%|███▊      | 19/50 [00:00<00:01, 30.04it/s]

Generating walks (CPU: 1):  46%|████▌     | 23/50 [00:00<00:00, 30.57it/s]

Generating walks (CPU: 1):  54%|█████▍    | 27/50 [00:00<00:00, 31.06it/s]

Generating walks (CPU: 1):  62%|██████▏   | 31/50 [00:01<00:00, 29.70it/s]

Generating walks (CPU: 1):  70%|███████   | 35/50 [00:01<00:00, 30.50it/s]

Generating walks (CPU: 1):  78%|███████▊  | 39/50 [00:01<00:00, 29.55it/s]

Generating walks (CPU: 1):  86%|████████▌ | 43/50 [00:01<00:00, 30.00it/s]

Generating walks (CPU: 1): 100%|██████████| 50/50 [00:01<00:00, 29.65it/s]

Processing Batches: 1

Number of train embeddings: 20
Number of validation embeddings: 2
Number of test embeddings: 2


Regression Task

In [47]:
print("Importing Libraries")
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import mean_squared_error
import numpy as np

Importing Libraries


In [48]:
print("Creating Embedding class")
class EmbeddingDataset(torch.utils.data.Dataset):
    def __init__(self, embeddings, targets):
        self.embeddings = embeddings
        self.targets = targets

    def __len__(self):
        return len(self.targets)

    def __getitem__(self, idx):
        return self.embeddings[idx], self.targets[idx]


Creating Embedding class


In [50]:
import torch

# Convert embeddings and targets to tensors
train_embeddings_tensor = torch.cat(train_embeddings)
train_targets_tensor = torch.tensor([data.y[0][0].item() for data in dataset[:1000]], dtype=torch.float32)
# Print the shapes and types of the tensors
print(f"Train embeddings tensor shape: {train_embeddings_tensor.shape}")
print(f"Train targets tensor shape: {train_targets_tensor.shape}")
print(f"Train embeddings tensor dtype: {train_embeddings_tensor.dtype}")
print(f"Train targets tensor dtype: {train_targets_tensor.dtype}")


Train embeddings tensor shape: torch.Size([12319, 64])
Train targets tensor shape: torch.Size([1000])
Train embeddings tensor dtype: torch.float32
Train targets tensor dtype: torch.float32


In [52]:

val_embeddings_tensor = torch.cat(val_embeddings)
val_targets_tensor = torch.tensor([data.y[0][0].item() for data in dataset[1000:1100]], dtype=torch.float32)
print(f"Validation embeddings tensor shape: {val_embeddings_tensor.shape}")
print(f"Validation targets tensor shape: {val_targets_tensor.shape}")
print(f"Validation embeddings tensor dtype: {val_embeddings_tensor.dtype}")
print(f"Validation targets tensor dtype: {val_targets_tensor.dtype}")


Validation embeddings tensor shape: torch.Size([1516, 64])
Validation targets tensor shape: torch.Size([100])
Validation embeddings tensor dtype: torch.float32
Validation targets tensor dtype: torch.float32


In [53]:

test_embeddings_tensor = torch.cat(test_embeddings)
test_targets_tensor = torch.tensor([data.y[0][0].item() for data in dataset[1100:1200]], dtype=torch.float32)

print(f"Test embeddings tensor shape: {test_embeddings_tensor.shape}")
print(f"Test targets tensor shape: {test_targets_tensor.shape}")
print(f"Test embeddings tensor dtype: {test_embeddings_tensor.dtype}")
print(f"Test targets tensor dtype: {test_targets_tensor.dtype}")


Test embeddings tensor shape: torch.Size([1534, 64])
Test targets tensor shape: torch.Size([100])
Test embeddings tensor dtype: torch.float32
Test targets tensor dtype: torch.float32


In [54]:

print("Create DataLoaders")
train_dataset = EmbeddingDataset(train_embeddings_tensor, train_targets_tensor)
val_dataset = EmbeddingDataset(val_embeddings_tensor, val_targets_tensor)
test_dataset = EmbeddingDataset(test_embeddings_tensor, test_targets_tensor)


Create DataLoaders


In [55]:

print("Loader")
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)


Loader


/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [56]:
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import mean_squared_error
from tqdm.notebook import tqdm  # Import tqdm for progress visualization

print("Define the model class")
class RegressionNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(RegressionNN, self).__init__()
        self.fc1 = nn.Linear(input_dim, hidden_dim)
        self.fc2 = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = self.fc2(x)
        return x

print("Training function")
def train_model(model, train_loader, optimizer, criterion, device):
    model.train()
    total_loss = 0
    print("Starting training...")
    for embeddings, targets in tqdm(train_loader, desc="Training", unit="batch"):
        embeddings, targets = embeddings.to(device), targets.to(device)
        optimizer.zero_grad()
        outputs = model(embeddings)
        loss = criterion(outputs.squeeze(), targets)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    avg_loss = total_loss / len(train_loader)
    print(f"Training completed with average loss: {avg_loss:.4f}")

print("Evaluation function")
def evaluate_model(model, data_loader, device):
    model.eval()
    predictions = []
    targets = []
    print("Starting evaluation...")
    with torch.no_grad():
        for embeddings, target in tqdm(data_loader, desc="Evaluating", unit="batch"):
            embeddings, target = embeddings.to(device), target.to(device)
            output = model(embeddings)
            predictions.extend(output.squeeze().cpu().numpy())
            targets.extend(target.cpu().numpy())
    rmse = mean_squared_error(targets, predictions, squared=False)
    print(f"Evaluation completed with RMSE: {rmse:.4f}")
    return rmse

print("Initialize model, optimizer, and criterion")
input_dim = embedding_dimensions
hidden_dim = 128
output_dim = 1
model = RegressionNN(input_dim, hidden_dim, output_dim)
optimizer = optim.Adam(model.parameters(), lr=0.001)
criterion = nn.MSELoss()

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Device being utilized:", device)
model.to(device)

print("Train the model")
num_epochs = 30
for epoch in tqdm(range(num_epochs), desc="Epoch progress", unit="epoch"):
    print(f"\nEpoch {epoch+1}/{num_epochs}")
    train_model(model, train_loader, optimizer, criterion, device)
    val_rmse = evaluate_model(model, val_loader, device)
    print(f'Epoch {epoch+1}, Validation RMSE: {val_rmse:.4f}')


Define the model class
Training function
Evaluation function
Initialize model, optimizer, and criterion
Device being utilized: cpu
Train the model


Epoch progress:   0%|          | 0/30 [00:00<?, ?epoch/s]


Epoch 1/30
Starting training...


Training:   0%|          | 0/32 [00:00<?, ?batch/s]

Training completed with average loss: 3.9254
Starting evaluation...


...

Evaluation completed with RMSE: 1.7684
Epoch 29, Validation RMSE: 1.7684

Epoch 30/30
Starting training...


Training:   0%|          | 0/32 [00:00<?, ?batch/s]

Training completed with average loss: 1.4323
Starting evaluation...


Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]

Evaluation completed with RMSE: 1.7337
Epoch 30, Validation RMSE: 1.7337


In [57]:
test_rmse = evaluate_model(model, test_loader, device)
print(f'Test RMSE: {test_rmse}')

Starting evaluation...


Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]

Evaluation completed with RMSE: 1.6382
Test RMSE: 1.6381711959838867


## Part 2

In [43]:
# Load QM9 Dataset (Ensure you load it correctly using torch_geometric.datasets.QM9)
from torch_geometric.datasets import QM9

dataset_path = 'dataset'  # Make sure to set this correctly
dataset = QM9(root=dataset_path)

# Filter any invalid edges from the dataset
req_dataset = dataset[:1300]
dataset_filtered  = [filter_invalid_edges(data) for data in tqdm(req_dataset, desc="Edge Filtering", leave=False)]

# Create train, validation, and test DataLoader
train_loader = create_dataloader(dataset_filtered [:1000])  # Using a subset for demonstration
val_loader = create_dataloader(dataset_filtered [1000:1100], shuffle=False)
test_loader = create_dataloader(dataset_filtered [1100:1200], shuffle=False)

/usr/local/lib/python3.10/dist-packages/torch_geometric/data/dataset.py:238: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  if osp.exists(f) and torch.load(f) != _repr(self.p

In [15]:
print("Importing required libraries for task 2")
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch_geometric.nn import GCNConv, global_mean_pool
from torch_geometric.datasets import QM9
from torch_geometric.loader import DataLoader
from tqdm.notebook import tqdm

Importing required libraries for task 2


In [16]:
# Print statement before defining the model
print("Defining the GCN model class...")

# Define the GCN model
class GCN_2(nn.Module):
    def __init__(self, num_node_features_2, num_layers_2, hidden_channels_2):
        super(GCN_2, self).__init__()
        print(f"Initializing GCN model with {num_node_features_2} node features, "
              f"{num_layers_2} layers, and {hidden_channels_2} hidden channels.")
        self.conv_layers_2 = nn.ModuleList()
        self.conv_layers_2.append(GCNConv(num_node_features_2, hidden_channels_2))
        for _ in range(num_layers_2 - 1):
            self.conv_layers_2.append(GCNConv(hidden_channels_2, hidden_channels_2))
        self.lin_2 = nn.Linear(hidden_channels_2, 1)

    def forward(self, x_2, edge_index_2, batch_2):
        for conv_2 in self.conv_layers_2:
            x_2 = conv_2(x_2, edge_index_2)
            x_2 = F.relu(x_2)
        x_2 = global_mean_pool(x_2, batch_2)
        x_2 = self.lin_2(x_2)
        return x_2.view(-1)

Defining the GCN model class...


In [17]:
# Print statement before loading and preprocessing data
print("Loading and preprocessing the QM9 dataset...")

# Load and preprocess the QM9 dataset
dataset_2 = QM9(root='data/QM9')
print(f"QM9 dataset loaded with {dataset_2.num_node_features} node features and {dataset_2.data.y.shape[1]} targets.")
dataset_2.data.y = dataset_2.data.y[:, 0:1]  # Use only the first target (dipole moment)
print("Using only the first target (dipole moment) for regression.")


Loading and preprocessing the QM9 dataset...
QM9 dataset loaded with 11 node features and 19 targets.
Using only the first target (dipole moment) for regression.


/usr/local/lib/python3.10/dist-packages/torch_geometric/data/in_memory_dataset.py:300: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. The data of the dataset is already cached, so any modifications to `data` will not be reflected when accessing its elements. Clearing the cache now by removing all elements in `dataset._data_list`. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.warn(msg)
/usr/local/lib/python3.10/dist-packages/torch_geometric/data/in_memory_dataset.py:300: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warnin

In [18]:

# Split the dataset
print("Splitting the dataset into train, validation, and test sets...")
train_dataset_2 = dataset_2[:1000]
val_dataset_2 = dataset_2[1000:1100]
test_dataset_2 = dataset_2[1100:1200]


Splitting the dataset into train, validation, and test sets...


In [19]:

# Create data loaders
print("Creating data loaders for training, validation, and testing...")
train_loader_2 = DataLoader(train_dataset_2, batch_size=32, shuffle=True)
val_loader_2 = DataLoader(val_dataset_2, batch_size=32)
test_loader_2 = DataLoader(test_dataset_2, batch_size=32)


Creating data loaders for training, validation, and testing...


In [20]:

# Print statement before initializing the model and training setup
print("Initializing the model, optimizer, and loss function...")

# Initialize the model
model_2 = GCN_2(num_node_features_2=dataset_2.num_node_features, num_layers_2=4, hidden_channels_2=64)
print(f"Model initialized with {dataset_2.num_node_features} input features, "
      f"4 layers, and 64 hidden channels.")
optimizer_2 = torch.optim.Adam(model_2.parameters(), lr=0.01)
print("Optimizer initialized with Adam optimizer and learning rate 0.01.")
criterion_2 = nn.MSELoss()
print("Loss function initialized with Mean Squared Error Loss.")


Initializing the model, optimizer, and loss function...
Initializing GCN model with 11 node features, 4 layers, and 64 hidden channels.
Model initialized with 11 input features, 4 layers, and 64 hidden channels.
Optimizer initialized with Adam optimizer and learning rate 0.01.
Loss function initialized with Mean Squared Error Loss.


In [22]:

# Print statement before defining the training function
print("Defining the training function...")

# Training function
def train_2():
    model_2.train()
    total_loss_2 = 0
    for data_2 in tqdm(train_loader_2, desc="Training Epochs", unit="batch"):
        optimizer_2.zero_grad()
        out_2 = model_2(data_2.x, data_2.edge_index, data_2.batch)
        loss_2 = criterion_2(out_2, data_2.y.view(-1))
        loss_2.backward()
        optimizer_2.step()
        total_loss_2 += loss_2.item() * data_2.num_graphs
    return total_loss_2 / len(train_loader_2.dataset)


Defining the training function...


In [23]:

# Print statement before defining the evaluation function
print("Defining the evaluation function...")

# Evaluation function
def evaluate_2(loader_2):
    model_2.eval()
    total_error_2 = 0
    with torch.no_grad():
        for data_2 in tqdm(loader_2, desc="Evaluating", unit="batch"):
            out_2 = model_2(data_2.x, data_2.edge_index, data_2.batch)
            total_error_2 += ((out_2 - data_2.y.view(-1)) ** 2).sum().item()
    return torch.sqrt(torch.tensor(total_error_2 / len(loader_2.dataset)))


Defining the evaluation function...


In [24]:

# Print statement before the training loop
print("Starting the training loop...")

# Training loop
num_epochs_2 = 100
for epoch_2 in tqdm(range(num_epochs_2), desc="Epoch progress", unit="epoch"):
    loss_2 = train_2()
    train_rmse_2 = evaluate_2(train_loader_2)
    val_rmse_2 = evaluate_2(val_loader_2)
    if (epoch_2 + 1) % 10 == 0:
        print(f'-\tEpoch: {epoch_2 + 1:03d}, Loss: {loss_2:.4f}, Train RMSE: {train_rmse_2:.4f}, Val RMSE: {val_rmse_2:.4f}')


Starting the training loop...


Epoch progress:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training Epochs:   0%|          | 0/32 [00:00<?, ?batch/s]

Evaluating:   0%|          | 0/32 [00:00<?, ?batch/s]

Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]

...

Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]

Training Epochs:   0%|          | 0/32 [00:00<?, ?batch/s]

Evaluating:   0%|          | 0/32 [00:00<?, ?batch/s]

Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]

-	Epoch: 100, Loss: 1.1424, Train RMSE: 1.0739, Val RMSE: 1.2602


In [25]:
# Test the model
test_rmse_2 = evaluate_2(test_loader_2)
print(f'\nTest RMSE: {test_rmse_2:.4f}')

Evaluating:   0%|          | 0/4 [00:00<?, ?batch/s]


Test RMSE: 0.9799


## Part 3

In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch_geometric.nn import MessagePassing, global_mean_pool
from torch_geometric.datasets import QM9
from torch_geometric.loader import DataLoader
import torch_geometric.transforms as T
# from tqdm import tqdm  # Import tqdm for progress bars
from tqdm.notebook import tqdm

In [3]:
print("Creating EGATConv")
class EGATConv(MessagePassing):
    def __init__(self, in_channels, out_channels):
        super(EGATConv, self).__init__(aggr='add')  # 'Add' aggregation
        self.in_channels = in_channels
        self.out_channels = out_channels

        self.lin = nn.Linear(in_channels, out_channels)
        self.att = nn.Linear(2 * out_channels, 1)
        self.leaky_relu = nn.LeakyReLU(0.2)

    def forward(self, x, edge_index):
        x = self.lin(x)
        return self.propagate(edge_index, x=x)

    def message(self, x_j, x_i, edge_index):
        x_i = x_i[edge_index[0]]  # Source node features
        x_j = x_j[edge_index[1]]  # Target node features

        edge_features = torch.cat([x_i, x_j], dim=-1)

        e_ij = self.leaky_relu(self.att(edge_features)).squeeze(-1)

        attention = F.softmax(e_ij, dim=0)

        return attention.unsqueeze(-1) * x_j

    def update(self, aggr_out):
        return aggr_out

Creating EGATConv


In [4]:
print("Creating EGAT")
class EGAT(nn.Module):
    def __init__(self, num_node_features, num_layers, hidden_channels):
        super(EGAT, self).__init__()
        self.conv_layers = nn.ModuleList()
        self.conv_layers.append(EGATConv(num_node_features, hidden_channels))
        for _ in range(num_layers - 1):
            self.conv_layers.append(EGATConv(hidden_channels, hidden_channels))
        self.lin = nn.Linear(hidden_channels, 1)

    def forward(self, x, edge_index, batch):
        for conv in self.conv_layers:
            x = conv(x, edge_index)
            x = F.relu(x)
        x = global_mean_pool(x, batch)
        x = self.lin(x)
        return x.view(-1)

Creating EGAT


In [5]:
print("Load and preprocess the QM9 dataset_3")
dataset_3 = QM9(root='data/QM9')
dataset_3.data.y = dataset_3.data.y[:, 0:1]

print("Split the dataset_3")
train_dataset_3 = dataset_3[:1000]
val_dataset_3 = dataset_3[1000:1100]
test_dataset_3 = dataset_3[1100:1200]

print("Create data loaders")
train_loader_3 = DataLoader(train_dataset_3, batch_size=32, shuffle=True)
val_loader_3 = DataLoader(val_dataset_3, batch_size=32)
test_loader_3 = DataLoader(test_dataset_3, batch_size=32)


Load and preprocess the QM9 dataset_3


Extracting data/QM9/raw/qm9_v3.zip
Processing...
Using a pre-processed version of the dataset. Please install 'rdkit' to alternatively process the raw data.
Done!


Split the dataset_3
Create data loaders


/usr/local/lib/python3.10/dist-packages/torch_geometric/data/in_memory_dataset.py:300: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.warn(msg)


In [6]:
print("Initialize the model_3")
model_3 = EGAT(num_node_features=dataset_3.num_node_features, num_layers=4, hidden_channels=64)
optimizer_3 = torch.optim.Adam(model_3.parameters(), lr=0.01)
criterion_3 = nn.MSELoss()


Initialize the model_3


In [7]:
print("Training function")
def train_3():
    model_3.train()
    total_loss_3 = 0
    for data_3 in tqdm(train_loader_3, desc="Training",leave=False):
        optimizer_3.zero_grad()
        out_3 = model_3(data_3.x, data_3.edge_index, data_3.batch)
        loss_3 = criterion_3(out_3, data_3.y.view(-1))
        loss_3.backward()
        optimizer_3.step()
        total_loss_3 += loss_3.item() * data_3.num_graphs
    return total_loss_3 / len(train_loader_3.dataset)

Training function


In [8]:
print("Evaluation function")
def evaluate_3(loader_3):
    model_3.eval()
    total_error_3 = 0
    with torch.no_grad():
        for data_3 in tqdm(loader_3, desc="Evaluating",leave=False):
            out_3 = model_3(data_3.x, data_3.edge_index, data_3.batch)
            total_error_3 += ((out_3 - data_3.y.view(-1)) ** 2).sum().item()
    return torch.sqrt(torch.tensor(total_error_3 / len(loader_3.dataset)))

Evaluation function


In [9]:
# Training loop
num_epochs_3 = 100
for epoch_3 in tqdm(range(num_epochs_3), desc="Epoch progress", unit="epoch"):
    loss_3 = train_3()
    train_rmse_3 = evaluate_3(train_loader_3)
    val_rmse_3 = evaluate_3(val_loader_3)
    if (epoch_3 + 1) % 10 == 0:
        print(f'\t-Epoch: {epoch_3+1:03d}, Loss: {loss_3:.4f}, Train RMSE: {train_rmse_3:.4f}, Val RMSE: {val_rmse_3:.4f}')

# Test the model_3
test_rmse_3 = evaluate_3(test_loader_3)
print(f'\nTest RMSE: {test_rmse_3:.4f}')

Epoch progress:   0%|          | 0/100 [00:00<?, ?epoch/s]

Training:   0%|          | 0/32 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/32 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/4 [00:00<?, ?it/s]

Training:   0%|          | 0/32 [00:00<?, ?it/s]

...

Evaluating:   0%|          | 0/32 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/4 [00:00<?, ?it/s]

	-Epoch: 100, Loss: 2.1359, Train RMSE: 1.4613, Val RMSE: 1.5564


Evaluating:   0%|          | 0/4 [00:00<?, ?it/s]


Test RMSE: 1.5484


In [12]:
# Test the model
test_rmse = evaluate_3(test_loader_3)
print(f'\n\nTest RMSE: {test_rmse:.4f}')

Evaluating:   0%|          | 0/4 [00:00<?, ?it/s]



Test RMSE: 1.5484
